# Ball classifier based on caffe CNN
This notebook trains CNN for ball classification.

## Create dataset
execute [create_caffe_ball_dataset](./create_caffe_ball_dataset.ipynb) if necessary, please check parameters in [caffe_ball_param.py](./caffe_ball_param.py)

## Setup

In [19]:
from __future__ import division
import os
import sys
import numpy as np
import cv2
import lmdb

from ml_utils import get_png_files_from_folder, load_images, create_image_wall

caffe_root = os.environ.get('CAFFE_ROOT', None)
if not caffe_root:
    raise "Please set CAFFE ROOT!"


sys.path.insert(0, os.path.join(caffe_root, 'python'))
import caffe

# Train

In [20]:
from caffe import layers as L, params as P

def lenet(lmdb, batch_size=64, sample_shape=None):
    # our version of LeNet: a series of linear and simple nonlinear transformations
    n = caffe.NetSpec()
    if lmdb:
        n.data, n.label = L.Data(batch_size=batch_size, backend=P.Data.LMDB, source=lmdb,
                                 transform_param=dict(scale=1./255), ntop=2)
        n.conv1 = L.Convolution(n.data, kernel_size=kernel_size, num_output=4, weight_filler=dict(type='xavier'))
    else:
        n.conv1 = L.Convolution(bottom="data", kernel_size=kernel_size, num_output=4, weight_filler=dict(type='xavier'))
    
    n.pool1 = L.Pooling(n.conv1, kernel_size=2, stride=2, pool=P.Pooling.MAX)
    #n.conv2 = L.Convolution(n.pool1, kernel_size=3, num_output=4, weight_filler=dict(type='xavier'))
    #n.pool2 = L.Pooling(n.conv2, kernel_size=2, stride=2, pool=P.Pooling.MAX)
    n.ip1 = L.InnerProduct(n.pool1, num_output=4, weight_filler=dict(type='xavier'))
    n.relu1 = L.ReLU(n.ip1, in_place=True)
    n.ip2 = L.InnerProduct(n.relu1, num_output=2, weight_filler=dict(type='xavier'))
    if lmdb:
        n.loss = L.SoftmaxWithLoss(n.ip2, n.label)
    else:
        n.prob = L.Softmax(n.ip2)
    n_str = str(n.to_proto())
    
    if not lmdb:
        n_str = 'name: "CaffeNet"\ninput: "data"\ninput_shape {\n  dim: 1\n  dim: 1\n  dim: %d\n  dim: %d\n}\n' % sample_shape + n_str
    
    return n_str

In [21]:
with open('ball_train.prototxt', 'w') as f:
    f.write(str(lenet('ball_train_lmdb', 64)))

with open('ball_test.prototxt', 'w') as f:
    f.write(str(lenet('ball_test_lmdb', 100)))

In [22]:
solver = None
solver = caffe.SGDSolver('ball_solver.prototxt')

In [23]:
sample_shape_2 = solver.net.blobs['data'].data.shape[2:]
assert sample_shape_2 == sample_shape

In [24]:
with open('ball_caffe.prototxt', 'w') as f:
    f.write(str(lenet(None, sample_shape=sample_shape)))

In [25]:
# each output is (batch size, feature dim, spatial dim)
[(k, v.data.shape) for k, v in solver.net.blobs.items()]

[('data', (64, 1, 16, 16)),
 ('label', (64,)),
 ('conv1', (64, 4, 12, 12)),
 ('pool1', (64, 4, 6, 6)),
 ('ip1', (64, 4)),
 ('ip2', (64, 2)),
 ('loss', ())]

In [26]:
solver.solve()
solver.net.save("ball_caffe.caffemodel")

In [27]:
correct = 0
batch_size = solver.test_nets[0].blobs['data'].num
test_iters = 100
for i in range(test_iters):
    solver.test_nets[0].forward()
    correct += sum(solver.test_nets[0].blobs['ip2'].data.argmax(1) == solver.test_nets[0].blobs['label'].data)
accuracy = correct / (test_iters * batch_size)

print("Accuracy: {:.3f}".format(accuracy))

Accuracy: 0.988


# Test

In [28]:
mean_blob = caffe.proto.caffe_pb2.BlobProto()
mean_blob.ParseFromString(open("ball_train.mean.binaryproto").read())
mn = np.array( caffe.io.blobproto_to_array(mean_blob) )
mn = mn.reshape(1, sample_shape[0], sample_shape[1])

classifier = caffe.Classifier('ball_caffe.prototxt', 'ball_caffe.caffemodel',
                              mean=mn, input_scale=1/255.0, raw_scale=255)

In [29]:
#ball_files = get_png_files_from_folder("../../robocupspl_db/ball2016_train2/ball/")
#noball_files = get_png_files_from_folder("../../robocupspl_db/ball2016_train2/no_ball/")

In [30]:
ball_images = [caffe.io.load_image(f, False) for f in ball_files]
ball_p = classifier.predict(ball_images)
print ball_p.argmax(axis=1)
ball_correct = np.count_nonzero(ball_p.argmax(axis=1))
ball_accuracy = ball_correct / len(ball_p)
print ball_accuracy 

[1 1 1 1 1 1 1 1 1 1 1 1 1 0 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1
 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 0 1 1 1 1 1 1 1 1 1
 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 0 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 0 1 1
 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1
 1 1 1 1 1 1 1 1 1 1 0 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1
 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1
 1 1 1 1 1 1 1 0 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 0 0 1 1 1 1 1 1 1 1 0 1
 1]
0.965384615385


In [31]:
noball_images = [caffe.io.load_image(f, False) for f in noball_files]
noball_p = classifier.predict(noball_images)
noball_correct = len(noball_p) - np.count_nonzero(noball_p.argmax(axis=1))
noball_accuracy = noball_correct / len(noball_p)
print noball_accuracy

0.990623046468


In [32]:
total_accuracy = (noball_correct + ball_correct) / (len(ball_p) + len(noball_p))
print total_accuracy

0.989325953746


# Summary

In [33]:
print 'kernel_size', kernel_size

for k, v in solver.net.blobs.items():
    print (k, v.data.shape)

print 'train accuracy: ', accuracy
print 'ball2 test', '#noball', len(noball_p), "#ball", len(ball_p)
print 'no ball:', noball_accuracy, 'ball:', ball_accuracy, 'total:', total_accuracy

kernel_size 5
('data', (64, 1, 16, 16))
('label', (64,))
('conv1', (64, 4, 12, 12))
('pool1', (64, 4, 6, 6))
('ip1', (64, 4))
('ip2', (64, 2))
('loss', ())
train accuracy:  0.9876
ball2 test #noball 4799 #ball 260
no ball: 0.990623046468 ball: 0.965384615385 total: 0.989325953746
